# INSRM-2177

Ingest correc information to fiducial_fiber table <br>
using bitwise operator (1 = BROKEN, 2 = BAD, 4 = OUTER_RING)

# Imports

In [1]:
import matplotlib.pyplot as plt
import numpy as np
from ics.cobraCharmer.cobraCoach import visDianosticPlot
import pathlib
from importlib import reload 
reload(visDianosticPlot)

import pandas as pd
from opdb import opdb

import psycopg2
from sqlalchemy import create_engine
from pfs.utils.fiberids import FiberIds
from pfs.utils import butler 

import pfs.utils.coordinates.transform as transformUtils
from pfs.utils.coordinates.transform import PfiTransform
from pfs.utils.coordinates.transform import matchIds

import os
import yaml


In [6]:
conn_str = "postgresql://pfs@db-ics/opdb"
engine = create_engine(conn_str)

with engine.connect() as conn:
    fiducialFiber = pd.read_sql(f'''
        SELECT DISTINCT 
            *
        FROM fiducial_fiber
        ORDER BY
            fiducial_fiber_id
        -- limit 10
        ''', conn)


In [7]:
fiducialFiber

fiducial_fiber_id  field_on_pfi  ff_in_field ff_type  ff_id_in_type  \
0                   1             1            1   spoke              1   
1                   2             1            2   spoke              2   
2                   3             1            3   spoke              3   
3                   4             1            4   spoke              4   
4                   5             1            5   spoke              5   
..                ...           ...          ...     ...            ...   
91                 92             3           28    edge             14   
92                 93             3           29   agfid              1   
93                 94             3           30   agfid              2   
94                 95             3           31   agfid              3   
95                 96             3           32   agfid              4   

     version  mask  
0   20171111  None  
1   20171111  None  
2   20171111  None  
3   20171111  None  
4   20171111  None  
..       ...   ...  
91  20171111  None  
92  20171111  None  
93  20171111  None  
94  20171111  None  
95  20171111  None  

[96 rows x 7 columns]

In [12]:

instPath = os.path.join('/software/devel/chyan/pfs_instdata/')

fidFile = os.path.join(instPath,"data/pfi/fiducials/fiducial_positions.csv")
fiducials = pd.read_csv(fidFile,header=13)


In [21]:
fiducials['flag'].values.astype('int')

array([2, 2, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 4, 4, 4, 6, 2, 2, 0, 2, 2, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 6, 4, 1, 4, 2, 2,
       2, 2, 2, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2,
       2, 0, 0, 0, 4, 4, 4, 4])

In [29]:
from sqlalchemy import create_engine, text
import pandas as pd

# Connection string
conn_str = "postgresql://pfs@db-ics/opdb"
engine = create_engine(conn_str)

# Define the table name
table_name = 'fiducial_fiber'

# Define the column to check for NULL values
column_name = 'mask'

# The value to insert
values_to_insert = fiducials['flag'].values


# Convert numpy array to a list of native Python integers
values_to_insert = values_to_insert.tolist()

# Create a connection
with engine.connect() as connection:
    for value in values_to_insert:
        # First, find the id of the row to update
        select_query = text(f"""
            SELECT fiducial_fiber_id
            FROM {table_name}
            WHERE {column_name} IS NULL
            ORDER BY fiducial_fiber_id
            LIMIT 1
        """)
        result = connection.execute(select_query).fetchone()
        
        if result:
            row_id = result[0]
            
            # Then, update that specific row
            update_query = text(f"""
                UPDATE {table_name}
                SET {column_name} = :value
                WHERE fiducial_fiber_id = :id
            """)
            
            # Execute the update query
            connection.execute(update_query, value=int(value), id=row_id)
        else:
            # If no more NULL values, break out of the loop
            break

    # Commit the changes
    connection.commit()


ProgrammingError: (psycopg2.errors.InsufficientPrivilege) permission denied for relation fiducial_fiber

[SQL: 
                UPDATE fiducial_fiber
                SET mask = %(value)s
                WHERE fiducial_fiber_id = %(id)s
            ]
[parameters: {'value': 2, 'id': 1}]
(Background on this error at: https://sqlalche.me/e/14/f405)